## NYC complaints 311 Calls

In this notebook we will exploit Pandas to perform data analysis on a dataset of calls to 311 (municipal calls, not emergency) in the New York City area.

Download the data from [here](https://data.cityofnewyork.us/Social-Services/311-Service-Requests-from-2010-to-Present/erm2-nwe9) (Go to Export -> CSV). (**WARNING: > 16 GB of data**)

For this notebook, use on a smaller version of the data [here](https://drive.google.com/file/d/1EHYsxnN18LAKIPpZbtqjqCLi5hokG1ag/view?usp=sharing).

In [114]:
%matplotlib inline
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import re

plt.rcParams['figure.figsize'] = (15, 5)
complaints = pd.read_csv('311_small.csv')

/var/folders/b3/cjvms6c10k77tgv6k_rw3jbh0000gn/T/ipykernel_94136/1126259180.py:8: DtypeWarning: Columns (8,31,32,34,35,36,37) have mixed types. Specify dtype option on import or set low_memory=False.
  complaints = pd.read_csv('311_small.csv')


In [115]:
complaints.columns

Index(['Unique Key', 'Created Date', 'Closed Date', 'Agency', 'Agency Name',
       'Complaint Type', 'Descriptor', 'Location Type', 'Incident Zip',
       'Incident Address', 'Street Name', 'Cross Street 1', 'Cross Street 2',
       'Intersection Street 1', 'Intersection Street 2', 'Address Type',
       'City', 'Landmark', 'Facility Type', 'Status', 'Due Date',
       'Resolution Description', 'Resolution Action Updated Date',
       'Community Board', 'BBL', 'Borough', 'X Coordinate (State Plane)',
       'Y Coordinate (State Plane)', 'Open Data Channel Type',
       'Park Facility Name', 'Park Borough', 'Vehicle Type',
       'Taxi Company Borough', 'Taxi Pick Up Location', 'Bridge Highway Name',
       'Bridge Highway Direction', 'Road Ramp', 'Bridge Highway Segment',
       'Latitude', 'Longitude', 'Location'],
      dtype='object')

#### drop columns 

In [116]:
complaints.shape

(999999, 41)

In [117]:
columns_to_drop = ['Created Date', 'Closed Date', 'Agency', 'Agency Name',
       'Descriptor', 'Status', 'Due Date',
       'Resolution Description', 'Resolution Action Updated Date',
       'Community Board', 'BBL', 'Open Data Channel Type',
       'Park Facility Name', 'Park Borough', 'Vehicle Type',
       'Taxi Company Borough', 'Taxi Pick Up Location', 'Bridge Highway Name',
       'Bridge Highway Direction', 'Road Ramp', 'Bridge Highway Segment']
df = complaints.drop(columns=columns_to_drop)

In [118]:
df.shape

(999999, 20)

In [119]:
df['Incident Zip'].dtype

dtype('O')

In [120]:
df['Incident Zip'].isna().sum()

88509

Let's reduce this number.

# Part 1: basic conversions

In [121]:
all_zips = df['Incident Zip']

In [122]:
def float_and_str(x):
    """
    make sure to have only floats and strings. 
    Note: type(np.nan) = float64
    """
    try:
        return float(x)
    except:
        return str(x)
zip1 = all_zips.apply(lambda x: float_and_str(x))

In [123]:
zip1.apply(type).unique()

array([<class 'float'>, <class 'str'>], dtype=object)

In [124]:
# check what strings look like
zip1[zip1.apply(lambda x: isinstance(x, str))]

883       37214-0065
40092         NEWARK
40145     10423-0935
63485     90054-0807
64033     18773-9640
76409     08690-1717
90617     11797-9004
146452    44087-2340
154503           UNK
159120             ?
164769    91716-0500
166800       NO IDEA
179235    30353-0942
179493             ?
209339       UNKNOWN
244742    30092-2670
253124             *
329115             *
379814       UNKNOWN
392099    53566-8019
419089    12551-0831
505758    17108-0988
508559    17108-0988
511704       UNKNOWN
549824    85251-3643
606653    11590-5027
654119    11735-3946
682171    11802-9060
685967             *
688809    61702-3517
760548    55164-0437
924175    61702-3517
957902       UNKNOWN
983209    14225-1032
Name: Incident Zip, dtype: object

### Steps
  1. clean char strings to np.nan
  2. clean numeric string:
     * split on '-'
     * check against [ZIP CODES](https://bklyndesigns.com/new-york-city-zip-code/)
  3. populate missing data

### 1. Clean char strings to np.nan

In [125]:
def clean_strings(x):
    """
    Convert strings to np.nan
    """
    p1 = re.compile(r'[A-Z]+')  # any word
    p2 = re.compile(r'[*]+')    # * literal
    p3 = re.compile(r'[?]+')    # ? literal
    if isinstance(x, str):
        for p in [p1, p2, p3]:
            if re.search(p, x):
                return np.nan
    return x

In [126]:
zip2 = zip1.apply(lambda x: clean_strings(x))

In [127]:
zip2[zip2.apply(lambda x: isinstance(x, str))]

883       37214-0065
40145     10423-0935
63485     90054-0807
64033     18773-9640
76409     08690-1717
90617     11797-9004
146452    44087-2340
164769    91716-0500
179235    30353-0942
244742    30092-2670
392099    53566-8019
419089    12551-0831
505758    17108-0988
508559    17108-0988
549824    85251-3643
606653    11590-5027
654119    11735-3946
682171    11802-9060
688809    61702-3517
760548    55164-0437
924175    61702-3517
983209    14225-1032
Name: Incident Zip, dtype: object

### Clean  numeric strings
### 1. split on '-'

NYC Zip codes are 5 digits only

In [128]:
def split_on_dash(x):
    p_code = re.compile(r'^\d{5}')   # find a number 
    p = re.compile(r'-')
    try:
        if re.match(p_code, x) and re.search(p, x):
            tmp = x.split('-')[0]
            return float(tmp)
    except TypeError:
        return x

In [129]:
zip3 = zip2.apply(lambda x: split_on_dash(x))

In [130]:
zip3[zip3.apply(lambda x: isinstance(x, str))]

Series([], Name: Incident Zip, dtype: float64)

### 2. check against [ZIP CODES](https://bklyndesigns.com/new-york-city-zip-code/)

In [131]:
complaints.iloc[76409, 16]

'HAMILTON SQUARE'

In [132]:
complaints.iloc[146452, 16]

'TWINSBURG'

In [133]:
complaints.iloc[179235, 16]

'ATLANTA'

All outside NYC area... some noise

  * Manhattan: 10001-10282
  * Staten Island: 10301-10314
  * Bronx: 10451-10475
  * Queens: 11004-11109, 11351-11697
  * Brooklyn: 11201-11256
  
#### Invalid if:
  * x < 10001
  * 10282 < x < 10301
  * 10314 < x < 10451
  * 10475 < x < 11004
  * 11109 < x < 11201
  * 11256 < x < 11351
  * x > 11697
  

In [134]:
def clean_zip_ranges(x):
    # type(x) == float
    try: 
        code = int(x)
    except ValueError: # np.nan
        return np.nan
    if code < 10001 or code > 11697:
        return np.nan
    elif 10282 < code < 10301:
        return np.nan
    elif 10475 < code < 11004:
        return np.nan
    elif 11109 < code < 11201:
        return np.nan
    elif 11256 < code < 11351:
        return np.nan
    else:
        return code

In [135]:
zip4 = zip3.apply(lambda x: clean_zip_ranges(x))

In [136]:
zip4.shape

(999999,)

In [137]:
zip4.isna().sum()

89524

Weren't we suppose to reduce that?

In [138]:
zip4.dtypes

dtype('float64')

In [139]:
df['Incident Zip'] = zip4

### 3. populate missing data

In [140]:
place_desc = ['Incident Zip', 'Borough', 'Street Name', 
              'Cross Street 1', 'Cross Street 2', 
              'Intersection Street 1', 'Intersection Street 2', 
              'Address Type', 'City', 'Landmark', 'Facility Type']

In [141]:
df['Borough'].value_counts()

Borough
BROOKLYN         322885
QUEENS           240326
BRONX            182361
MANHATTAN        181866
STATEN ISLAND     53961
Unspecified       18502
Name: count, dtype: int64

In [142]:
unspec_boro = df['Borough'] == 'Unspecified'
df.loc[unspec_boro,'Borough'] = np.nan

In [143]:
df[place_desc].head(3)

Incident Zip   Borough     Street Name Cross Street 1   Cross Street 2  \
0       11226.0  BROOKLYN  CLARENDON ROAD            NaN              NaN   
1           NaN       NaN             NaN            NaN              NaN   
2       11211.0  BROOKLYN  SOUTH 4 STREET  SOUTH 5 PLACE  ROEBLING STREET   

  Intersection Street 1 Intersection Street 2 Address Type      City Landmark  \
0                   NaN                   NaN      ADDRESS  BROOKLYN      NaN   
1                   NaN                   NaN          NaN       NaN      NaN   
2                   NaN                   NaN      ADDRESS  BROOKLYN      NaN   

  Facility Type  
0           NaN  
1           NaN  
2           NaN

In [144]:
df.dropna(how='all', subset=place_desc, inplace=True)

In [145]:
df.shape

(985714, 20)

In [146]:
for col in place_desc:
    print(f'{col :<22} {df[col].isna().sum() / df.shape[0] :.2%}')

Incident Zip           7.63%
Borough                0.44%
Street Name            13.21%
Cross Street 1         46.00%
Cross Street 2         46.20%
Intersection Street 1  87.36%
Intersection Street 2  87.38%
Address Type           7.04%
City                   7.59%
Landmark               98.89%
Facility Type          71.68%


In [147]:
# some useful filters
is_brooklyn = df['Borough'] == 'BROOKLYN'
is_manhattan = df['Borough'] == 'MANHATTAN'
is_queens = df['Borough'] == 'QUEENS'
is_bronx = df['Borough'] == 'BRONX'
is_staten = df['Borough'] == 'STATEN ISLAND'

In [148]:
def inspect(borough_mask, group_list, target):
    """
    Return a dataframe of per borough groups of distinct `group_list`
    attributes counting the number of `target` per group.
    """
    tmp = df.loc[borough_mask, place_desc]
    tmp['count'] = tmp.groupby(group_list)[target].transform('count')
    tmp.sort_values(by='Street Name', inplace=True)
    return tmp

In [149]:
group = ['Incident Zip', 'Street Name', 'City']
target = 'Street Name'
inspect(is_brooklyn, group, target).head()

Incident Zip   Borough  Street Name Cross Street 1 Cross Street 2  \
396356           NaN  BROOKLYN  .DEKALB AVE            NaN            NaN   
455159           NaN  BROOKLYN     1 AVENUE            NaN            NaN   
551777       11232.0  BROOKLYN     1 AVENUE      40 STREET      41 STREET   
170575       11220.0  BROOKLYN     1 AVENUE      54 STREET      55 STREET   
669247       11220.0  BROOKLYN     1 AVENUE      56 STREET      57 STREET   

       Intersection Street 1 Intersection Street 2 Address Type      City  \
396356                   NaN                   NaN          NaN       NaN   
455159                   NaN                   NaN          NaN       NaN   
551777                   NaN                   NaN      ADDRESS  BROOKLYN   
170575             54 STREET             55 STREET          NaN  BROOKLYN   
669247                   NaN                   NaN      ADDRESS  BROOKLYN   

        Landmark Facility Type  count  
396356       NaN           NaN    NaN  
455159       NaN           NaN    NaN  
551777       NaN      Precinct   17.0  
170575  1 AVENUE           NaN   11.0  
669247       NaN           NaN   11.0

In [150]:
# clean r'^\.'
df[df['Street Name'].str.match(r'^\.', na=False)]['Street Name']

396356    .DEKALB AVE
615835              .
Name: Street Name, dtype: object

In [151]:
df.loc[615835, 'Street Name'] = np.nan
df.loc[396356, 'Street Name'] = 'DEKALB AVE'

In [152]:
def find_all_zips(borough_mask):
    streets = df.loc[borough_mask, 'Street Name'].unique()
    multiple_zips = {}
    for street in streets:
        mask = df['Street Name'] == street
        street_to_zips = df.loc[(borough_mask & mask), 'Incident Zip'].unique()
        # sub-optimal: pick up ONLY when 2 alternative: [zipcode np.nan]
        if (len(street_to_zips) == 2) and (np.isnan(street_to_zips.sum())):
            multiple_zips[street] = street_to_zips
    return multiple_zips

#### Let's start with Brooklyn

In [153]:
all_zips = find_all_zips(is_brooklyn)
print(len(all_zips))

864


In [154]:
all(len(zips) == 2 for _, zips in all_zips.items())

True

In [155]:
for k, v in all_zips.items():
    print(k, v)
    print(np.argwhere(~np.isnan(v)))
    print(v[np.argwhere(~np.isnan(v))[0][0]])
    break

95 STREET [11209.    nan]
[[0]]
11209.0


In [156]:
brooklyn_zips = [(street, zips[np.argwhere(~np.isnan(zips))[0][0]]) 
                for street, zips in all_zips.items()]

In [157]:
brooklyn_zips[0]

('95 STREET', 11209.0)

In [158]:
for street, zipcode in brooklyn_zips:
    mask = df['Street Name'] == street
    df.loc[(is_brooklyn & mask), 'Incident Zip'] = zipcode   # UPDATE IN PLACE THE ORIGINAL DATAFRAME

### Prototype and doit for all other boroughs

In [159]:
def doit(boro_mask):
    all_zips = find_all_zips(boro_mask)
    print(f"Found {len(all_zips)} street names in {df[boro_mask]['Borough'].unique()}")
    boro_zips = [(street, zips[np.argwhere(~np.isnan(zips))[0][0]]) 
                for street, zips in all_zips.items()]
    for street, zipcode in boro_zips:
        mask = df['Street Name'] == street
        df.loc[(boro_mask & mask), 'Incident Zip'] = zipcode

In [160]:
for m in [is_manhattan, is_staten, is_bronx, is_queens]:  # all boroughs except BROOKLYN
    doit(m)

Found 143 street names in ['MANHATTAN']
Found 880 street names in ['STATEN ISLAND']
Found 628 street names in ['BRONX']
Found 721 street names in ['QUEENS']


## After the first pass:

In [161]:
df.dropna(how='all', subset=place_desc, inplace=True)
df.shape

(985714, 20)

In [162]:
df['Incident Zip'].isna().sum()

61237

Better...
However this method has serious drawbacks in terms of performances.

In [164]:
# Save your efforts...
df.to_csv('311_almost_cleaned.csv', index=False)   # index = False so we dont have to manage it next time